<h1>Geographical Analysis of Tweets</h1>

<b>Tasks:</b>
<ol>
<li>Import may 5th tweets</li>
<li>Carry out sentiment analysis of the tweets</li>
<li>Geocode the tweets based on user location</li>
<li>Plot them on a map based on Sentiment</li>
</ol>

In [1]:
import pandas as pd
#Read in the previously built dataframe of may 5th data
df = pd.read_csv('may_5_tweets.csv')
df.head()

created_at  \
0  2020-05-05 11:14:28+00:00   
1  2020-05-05 11:14:29+00:00   
2  2020-05-05 11:14:29+00:00   
3  2020-05-05 11:14:29+00:00   
4  2020-05-05 11:14:29+00:00   

                                                text lang  \
0  RT @ASlavitt: BREAKING: The organization Trump...   en   
1  RT @Therinesky: 11,000 ABS-CBN employees are b...   en   
2  RT @MidwivesRCM: Midwives &amp;  UK maternity ...   en   
3  A Storm Is Brewing\n\n#QAnon #WWG1WGA #TheGrea...   en   
4  RT @gtconway3d: I guess we know what keeps the...   en   

                                  quoted_status-text  retweeted_status-text  \
0                                                NaN                    NaN   
1                                                NaN                    NaN   
2                                                NaN                    NaN   
3                                                NaN                    NaN   
4  A group of RINO Republicans who failed badly 1...                    NaN   

                                            all_text determined_location  \
0  RT @ASlavitt: BREAKING: The organization Trump...      Cocoa, Florida   
1  RT @Therinesky: 11,000 ABS-CBN employees are b...              Manila   
2  RT @MidwivesRCM: Midwives &amp;  UK maternity ...      Leeds, England   
3  A Storm Is Brewing\n\n#QAnon #WWG1WGA #TheGrea...         Zachary, LA   
4  RT @gtconway3d: I guess we know what keeps the...      Pittsburgh, PA   

   deaths_mention  recovery_mention  
0            True             False  
1           False             False  
2           False             False  
3           False             False  
4           False             False

Perform sentiment analysis

In [2]:
# perform sentiment analysis for covid tweet
from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid  = SentimentIntensityAnalyzer()

In [3]:
sentiment_score_text = df['text'].apply(sid.polarity_scores) 
sentiment = sentiment_score_text.apply(lambda x: x['compound'])

In [4]:
df['sentiment']= sentiment
df.head()

created_at  \
0  2020-05-05 11:14:28+00:00   
1  2020-05-05 11:14:29+00:00   
2  2020-05-05 11:14:29+00:00   
3  2020-05-05 11:14:29+00:00   
4  2020-05-05 11:14:29+00:00   

                                                text lang  \
0  RT @ASlavitt: BREAKING: The organization Trump...   en   
1  RT @Therinesky: 11,000 ABS-CBN employees are b...   en   
2  RT @MidwivesRCM: Midwives &amp;  UK maternity ...   en   
3  A Storm Is Brewing\n\n#QAnon #WWG1WGA #TheGrea...   en   
4  RT @gtconway3d: I guess we know what keeps the...   en   

                                  quoted_status-text  retweeted_status-text  \
0                                                NaN                    NaN   
1                                                NaN                    NaN   
2                                                NaN                    NaN   
3                                                NaN                    NaN   
4  A group of RINO Republicans who failed badly 1...                    NaN   

                                            all_text determined_location  \
0  RT @ASlavitt: BREAKING: The organization Trump...      Cocoa, Florida   
1  RT @Therinesky: 11,000 ABS-CBN employees are b...              Manila   
2  RT @MidwivesRCM: Midwives &amp;  UK maternity ...      Leeds, England   
3  A Storm Is Brewing\n\n#QAnon #WWG1WGA #TheGrea...         Zachary, LA   
4  RT @gtconway3d: I guess we know what keeps the...      Pittsburgh, PA   

   deaths_mention  recovery_mention  sentiment  
0            True             False     0.0000  
1           False             False    -0.6597  
2           False             False     0.0000  
3           False             False     0.0000  
4           False             False     0.4215

In [5]:
print(df['sentiment'].max(), df['sentiment'].min())

0.9834 -0.9756


Geocode the tweets based on user location description

In [6]:
import math
import geopandas as gpd
from geopandas.tools import geocode

import folium 
from folium import Marker
from folium.plugins import MarkerCluster

In [7]:
df = df.sample(n=5000, random_state=1)

In [8]:
def my_geocoder(row):
    try:
        point = geocode(row, provider='nominatim', ).geometry.iloc[0]
        return pd.Series({'Latitude': point.y, 'Longitude': point.x, 'geometry': point})
    except:
        return None

locations_decoded = df[['determined_location']].apply(lambda x: my_geocoder(x), axis=1)


In [9]:
import numpy as np
print('The percentage of places geocoded is {}'.format(sum(~np.isnan(locations_decoded['Latitude']))*100/len(df)))

The percentage of places geocoded is 90.42


This is a good number to plot on the map although the data is 100% not realiable

In [10]:
locations_decoded.reset_index(inplace=True)
locations_decoded = locations_decoded[locations_decoded['Latitude'].notnull()]
df_with_location = pd.merge(df.reset_index(), locations_decoded, how='right', left_index=True, right_index=True)
df_with_location = gpd.GeoDataFrame(df_with_location, geometry=df_with_location.geometry)
df_with_location.crs = {'init': 'epsg:4326'}
df_with_location.head()

index_x                 created_at  \
0     5633  2020-05-05 11:18:11+00:00   
1     5769  2020-05-05 11:18:16+00:00   
2     2625  2020-05-05 11:16:12+00:00   
3     2615  2020-05-05 11:16:12+00:00   
4     6434  2020-05-05 11:18:43+00:00   

                                                text lang  \
0  RT @JOYNEWSONTV: (((LIVE: Ministry of Informat...   en   
1  RT @nspector4: Basically, the @JustinTrudeau g...   en   
2  COVID-10 cases nearing 100,000 in Iran https:/...   en   
3  RT @TeaPainUSA: Tea’s gonna be straight with y...   en   
4  RT @ashindestad: You won Britain. Enjoy the de...   en   

                                  quoted_status-text  retweeted_status-text  \
0                                                NaN                    NaN   
1  Most of Canada’s cases in late February and ea...                    NaN   
2                                                NaN                    NaN   
3  BREAKING: The organization Trump used to proje...                    NaN   
4  UK now has highest coronavirus death toll in E...                    NaN   

                                            all_text determined_location  \
0  RT @JOYNEWSONTV: (((LIVE: Ministry of Informat...               accra   
1  RT @nspector4: Basically, the @JustinTrudeau g...     Barrie, Ontario   
2  COVID-10 cases nearing 100,000 in Iran https:/...          Azerbaijan   
3  RT @TeaPainUSA: Tea’s gonna be straight with y...        Florida, USA   
4  RT @ashindestad: You won Britain. Enjoy the de...     London, England   

   deaths_mention  recovery_mention  sentiment  index_y   Latitude  Longitude  \
0           False             False     0.0000     5633   5.560014  -0.205744   
1           False             False     0.0000     5769  44.389311 -79.690174   
2           False             False     0.0000     2625  40.393629  47.787251   
3            True             False    -0.4588     2615  27.756767 -81.463983   
4            True             False     0.8648     6434  51.507322  -0.127647   

                     geometry  
0    POINT (-0.20574 5.56001)  
1  POINT (-79.69017 44.38931)  
2   POINT (47.78725 40.39363)  
3  POINT (-81.46398 27.75677)  
4   POINT (-0.12765 51.50732)

Here is a map with the tweets plotted on each location, we can then do some sentiment analysis and we can see 
how it matches to policy stringency data. 

In [11]:
#m = folium.Map(location=[30, 0], zoom_start=2)

#for idx, row in df_with_location.iterrows():
#    Marker([row.Latitude, row.Longitude], popup=row['text']).add_to(m)   
#m
#import branca
#import branca.colormap as cm
#colormap = cm.LinearColormap(colors=['red','green'], index=[-1,1],vmin=-1,vmax=1)

In [12]:
def color_producer(val):
    if val < -0.6:
        return 'red'
    if val > 0.6:
        return 'green'
    else:
        return 'yellow'
 
m_2 = folium.Map(location=[30, 0], zoom_start=2) 

for idx, row in df_with_location.iterrows():
    folium.Circle(location=[row['Latitude'], row['Longitude']], radius=10, 
                  color=color_producer(row['sentiment']), popup=row['text']).add_to(m_2)
m_2